# Time Series Forecasting with XGBoost

In [1]:
import pandas as pd
import numpy as np
import xgboost as xgb
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_squared_error


## Read **Data**

In [2]:
df = pd.read_csv('PJME_hourly.csv')
print(df.shape)
print(df.dtypes)
df.head()

(145366, 2)
Datetime     object
PJME_MW     float64
dtype: object


Datetime  PJME_MW
0  2002-12-31 01:00:00  26498.0
1  2002-12-31 02:00:00  25147.0
2  2002-12-31 03:00:00  24574.0
3  2002-12-31 04:00:00  24393.0
4  2002-12-31 05:00:00  24860.0

In [3]:
df.Datetime = pd.to_datetime(df.Datetime,format="%Y-%m-%d")
df.dtypes

Datetime    datetime64[ns]
PJME_MW            float64
dtype: object

In [4]:
df.Datetime.agg([min, max])

min   2002-01-01 01:00:00
max   2018-08-03 00:00:00
Name: Datetime, dtype: datetime64[ns]

In [5]:
df = df[df.Datetime <"2018-08-01"]
df.shape

(145317, 2)

In [6]:
df = df.set_index('Datetime')

In [7]:
df['Year'] = df.index.year 
df['Month'] = df.index.month 
df['Day'] = df.index.day 
df['weekday'] = df.index.weekday
df['hour']  = df.index.hour
df['week_num']= df.index.week
df['quarter'] = df.index.quarter
df['dayofyear'] = df.index.dayofyear
df.head()

<ipython-input-7-4367cffd37a7>:6: FutureWarning: weekofyear and week have been deprecated, please use DatetimeIndex.isocalendar().week instead, which returns a Series.  To exactly reproduce the behavior of week and weekofyear and return an Index, you may call pd.Int64Index(idx.isocalendar().week)
  df['week_num']= df.index.week


PJME_MW  Year  Month  Day  weekday  hour  week_num  \
Datetime                                                                  
2002-12-31 01:00:00  26498.0  2002     12   31        1     1         1   
2002-12-31 02:00:00  25147.0  2002     12   31        1     2         1   
2002-12-31 03:00:00  24574.0  2002     12   31        1     3         1   
2002-12-31 04:00:00  24393.0  2002     12   31        1     4         1   
2002-12-31 05:00:00  24860.0  2002     12   31        1     5         1   

                     quarter  dayofyear  
Datetime                                 
2002-12-31 01:00:00        4        365  
2002-12-31 02:00:00        4        365  
2002-12-31 03:00:00        4        365  
2002-12-31 04:00:00        4        365  
2002-12-31 05:00:00        4        365

In [8]:
df.week_num.agg(['min','max'])

min     1
max    53
Name: week_num, dtype: int64

In [9]:
# df_year = df.groupby(['Year']).agg({"PJME_MW": lambda x: x.sum()})
# # df_year.reset_index(inplace=True)
# print(df_year.shape)

# df_year_month = df.groupby(['Year','Month']).agg({"PJME_MW":'sum'})
# df_year_month.reset_index(inplace=True)
# df_year_month['Year-Month'] = df_year_month['Year'].astype(str)+'-'+df_year_month['Month'].astype(str)
# print(df_year_month.shape) # 12*16+8

# df_daily = df.groupby(['Year','Month','Day']).agg({"PJME_MW":'sum'})
# df_daily.reset_index(inplace=True)
# df_daily['Date'] = pd.to_datetime(dict(year=df_daily.Year,month=df_daily.Month,day=df_daily.Day))
# print(df_daily.shape)

# df_weekly = df.groupby(['Year','week_num']).agg({"PJME_MW":'sum'})
# df_weekly.reset_index(inplace=True)
# df_weekly['Year-Week'] = df_weekly['Year'].astype(str)+'-'+df_weekly['week_num'].astype(str)
# print(df_weekly.shape)  # 16.7*52

# df_weekday= df.groupby(['weekday']).agg({"PJME_MW":'sum'})
# df_weekday.reset_index(inplace=True)
# print(df_weekday.head())
# print(df_weekday.shape)

# df_week = df.groupby(['week_num']).agg({"PJME_MW":'sum'})
# df_week.reset_index(inplace=True)
# df_quarterofyear = df.groupby(['quarter']).agg({"PJME_MW":'sum'})
# df_quarterofyear.reset_index(inplace=True)
# df_dayofyear = df.groupby(['dayofyear']).agg({"PJME_MW":'sum'})
# df_dayofyear.reset_index(inplace=True)

# df_quarterly =df.groupby(['Year','quarter']).agg({"PJME_MW":"sum"})
# df_quarterly.reset_index(inplace=True)
# df_quarterly['Year-Quarter'] = df_quarterly['Year'].astype(str)+'-'+df_quarterly['quarter'].astype(str)
# print(df_quarterly.shape)
# print(df_quarterly.head())


## Consumption Analysis

In [10]:
fig1 = make_subplots(rows=2, cols=2,
                     subplot_titles=("Hourly Consumption", 
                                     "Day of Week Consumption",
                                     "Month of Year Consumption",
                                     "Quarter of Year Consumption",
                                     )
                     )

fig1.add_trace(
    go.Box(x=df['hour'], y=df['PJME_MW']),
    row=1,col=1
)

fig1.add_trace(
    go.Box(x=df['weekday'], y=df['PJME_MW']),
    row=1,col=2
)
fig1.add_trace(
    go.Box(x=df['Month'], y=df['PJME_MW']),
    row=2,col=1
)
fig1.add_trace(
    go.Box(x=df['quarter'], y=df['PJME_MW']),
    row=2,col=2
)

fig1.update_layout(showlegend=False, title_text="Energy Consumption",title_x=0.5)
fig1.show()

## Split Data

In [11]:
cutoff_date = "2015-01-01"
features = ['Year','Month','Day','weekday','hour','week_num','quarter','dayofyear']

X = df.loc[:,features]
y = df.loc[:,'PJME_MW']

# split data into train and test set
X_train= X[X.index < cutoff_date]
X_test = X[X.index >= cutoff_date]

y_train = y[y.index<cutoff_date]
y_test = y[y.index>=cutoff_date]

print(X_train.shape,y_train.shape)
print(X_test.shape, y_test.shape)

(113926, 8) (113926,)
(31391, 8) (31391,)


## XGBoost Hyperparameter tuning using GridSearchCV 

In [12]:
parameters = {
            'learning_rate': [0.05, 0.01],
            'max_depth': [5, 7],
            'n_estimator':[1000,1500],
            'early_stopping_rounds':[50, 70],
            'base_score':[0.5,0.7],
            'booster':['gbtree'],
            'random_state':[42],
            'objective':['reg:squarederror'],

}
xgb1 = xgb.XGBRegressor()
xgb1_grid = GridSearchCV(xgb1,parameters, n_jobs=5)
xgb1_grid.fit(X_train,y_train)
print(xgb1_grid.best_score_)
print(xgb1_grid.best_params_)

0.72024959566376
{'base_score': 0.7, 'booster': 'gbtree', 'early_stopping_rounds': 50, 'learning_rate': 0.05, 'max_depth': 5, 'n_estimator': 1000, 'objective': 'reg:squarederror', 'random_state': 42}


In [13]:
xgb1_grid.best_estimator_.get_params

<bound method XGBModel.get_params of XGBRegressor(base_score=0.7, early_stopping_rounds=50, learning_rate=0.05,
             max_depth=5, n_estimator=1000, objective='reg:squarederror',
             random_state=42)>

## Predict Energy Consumption

In [14]:
y_pred1 = pd.DataFrame(xgb1_grid.best_estimator_.predict(X_test),columns=['prediction'])

y_pred1

prediction
0      32546.425781
1      28647.472656
2      27504.339844
3      27160.179688
4      27160.179688
...             ...
31386  37278.222656
31387  37271.324219
31388  36468.820312
31389  34577.781250
31390  32558.396484

[31391 rows x 1 columns]

In [15]:
res1 = pd.concat([y_test.reset_index(),y_pred1],axis=1)
res1

Datetime  PJME_MW    prediction
0     2015-01-01 00:00:00  32802.0  32546.425781
1     2015-12-31 01:00:00  24305.0  28647.472656
2     2015-12-31 02:00:00  23156.0  27504.339844
3     2015-12-31 03:00:00  22514.0  27160.179688
4     2015-12-31 04:00:00  22330.0  27160.179688
...                   ...      ...           ...
31386 2018-01-01 20:00:00  44284.0  37278.222656
31387 2018-01-01 21:00:00  43751.0  37271.324219
31388 2018-01-01 22:00:00  42402.0  36468.820312
31389 2018-01-01 23:00:00  40164.0  34577.781250
31390 2018-01-02 00:00:00  38608.0  32558.396484

[31391 rows x 3 columns]

## Performance metric - Mean Squared Error

In [16]:
rmse_score1 = np.sqrt(mean_squared_error(res1['PJME_MW'],res1['prediction']))
rmse_score1

3697.514181068024

## Visualization: Actual vs Predicted 

In [17]:
res1.rename(columns={'PJME_MW':'Acutal'},inplace=True)
fig1 = px.line(res1,x='Datetime',y=res1.columns)
fig1.show()

## Feature Importance

In [18]:
fimp = pd.DataFrame(data = xgb1_grid.best_estimator_.feature_importances_,
             index = xgb1_grid.best_estimator_.get_booster().feature_names,
             columns=['weight'])
fimp = fimp.sort_values(by=['weight'],ascending=False)
fimp

weight
Month      0.335816
hour       0.331884
weekday    0.150191
dayofyear  0.114827
week_num   0.036315
Year       0.017973
Day        0.012993
quarter    0.000000

In [19]:
fig2 = px.bar(fimp, y="weight", title="Feature Importance")
fig2.update_layout(title_x=0.5, xaxis_title="feature")
fig2.show()